In [0]:
%run ../_utils

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
  Using cached Unidecode-1.3.8-py3-none-any.whl (235 kB)
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
from pyspark.sql.functions import when, to_date, col, dayofweek
from pyspark.sql.types import StringType, BooleanType


# Camada Silver

Na camada silver, limpezas e ajustes em dados devem ser aplicados

Caso seja possível, enriquecer os dados e extrair dados também deve acontecer nessa camada (minha definição)

In [0]:
tb_name = "olist_silver.order_reviews"
dataset_location = "olist_order_reviews_dataset"
target_location = f"dbfs:/FileStore/delta/brazilian_ecommerce/{dataset_location}/silver"

## 1 - Data ingestion

In [0]:
df = spark.read.table("olist_bronze.order_reviews") # leituira da delta table

In [0]:
df.printSchema()

root
 |-- review_id: string (nullable = true)
 |-- order_id: string (nullable = true)
 |-- review_score: integer (nullable = true)
 |-- review_comment_title: string (nullable = true)
 |-- review_comment_message: string (nullable = true)
 |-- review_creation_date: timestamp (nullable = true)
 |-- review_answer_timestamp: timestamp (nullable = true)



In [0]:
display(df)

review_id order_id review_score review_comment_title review_comment_message review_creation_date review_answer_timestamp 7bc2406110b926393aa56f80a40eba40 73fc7af87114b39712e6da79b0a377eb 4 null null 2018-01-18T00:00:00Z 2018-01-18T21:46:59Z 80e641a11e56f04c1ad469d5645fdfde a548910a1c6147796b98fdf73dbeba33 5 null null 2018-03-10T00:00:00Z 2018-03-11T03:05:13Z 228ce5500dc1d8e020d8d1322874b6f0 f9e4b658b201a9f2ecdecbb34bed034b 5 null null 2018-02-17T00:00:00Z 2018-02-18T14:36:24Z e64fb393e7b32834bb789ff8bb30750e 658677c97b385a9be170737859d3511b 5 null Recebi bem antes do prazo estipulado. 2017-04-21T00:00:00Z 2017-04-21T22:02:06Z f7c4243c7fe1938f181bec41a392bdeb 8e6bfb81e283fa7e4f11123a3fb894f1 5 null Parabéns lojas lannister adorei comprar pela Internet seguro e prático Parabéns a todos feliz Páscoa 2018-03-01T00:00:00Z 2018-03-02T10:26:53Z 15197aa66ff4d0650b5434f1b46cda19 b18dcdf73be66366873cd26c5724d1dc 1 null null 2018-04-13T00:00:00Z 2018-04-16T00:39:37Z 07f9bee5d1b850860defd761afa7ff16 e48aa0d2dcec3a2e87348811bcfdf22b 5 null null 2017-07-16T00:00:00Z 2017-07-18T19:30:34Z 7c6400515c67679fbee952a7525281ef c31a859e34e3adac22f376954e19b39d 5 null null 2018-08-14T00:00:00Z 2018-08-14T21:36:06Z a3f6f7f6f433de0aefbb97da197c554c 9c214ac970e84273583ab523dfafd09b 5 null null 2017-05-17T00:00:00Z 2017-05-18T12:05:37Z 8670d52e15e00043ae7de4c01cc2fe06 b9bf720beb4ab3728760088589c62129 4 recomendo aparelho eficiente. no site a marca do aparelho esta impresso como 3desinfector e ao chegar esta com outro nome...atualizar com a marca correta uma vez que é o mesmo aparelho 2018-05-22T00:00:00Z 2018-05-23T16:45:47Z c9cfd2d5ab5911836ababae136c3a10c cdf9aa68e72324eeb25c7de974696ee2 5 null null 2017-12-23T00:00:00Z 2017-12-26T14:36:03Z 96052551d87e5f62e6c9f6974ec392e9 3d374c9e46530bb5ed4a7648915306a6 5 null null 2017-12-19T00:00:00Z 2017-12-20T10:25:22Z 4b49719c8a200003f700d3d986ea1a19 9d6f15f95d01e79bd1349cc208361f09 4 null Mas um pouco ,travando...pelo valor ta Boa.
 2018-02-16T00:00:00Z 2018-02-20T10:52:22Z 23f75a37effc35d9a915b4e1ad483793 2eaf8e099d871cd5c22b83b5ea8f6e0e 4 null null 2018-03-28T00:00:00Z 2018-03-30T15:10:55Z 9a0abbb668bafb95a6d2b05db43284c4 d7bd0e4afdf94846eb73642b4e3e75c3 3 null null 2017-04-30T00:00:00Z 2017-05-03T00:02:22Z 3948b09f7c818e2d86c9a546758b2335 e51478e7e277a83743b6f9991dbfa3fb 5 Super recomendo Vendedor confiável, produto ok e entrega antes do prazo. 2018-05-23T00:00:00Z 2018-05-24T03:00:01Z 9314d6f9799f5bfba510cc7bcd468c01 0dacf04c5ad59fd5a0cc1faa07c34e39 2 null GOSTARIA DE SABER O QUE HOUVE, SEMPRE RECEBI E ESSA COMPRA AGORA ME DECPCIONOU 2018-01-18T00:00:00Z 2018-01-20T21:25:45Z 8e15a274d95600fa14f8be64e37a0e67 ff1581e08b3011021e7c7de592ddc81e 5 null null 2018-03-24T00:00:00Z 2018-03-26T15:58:32Z fdbdb2629a7cde0f66657acc92084e7f 70a752414a13d09cc1f2b437b914b28e 3 null null 2017-09-29T00:00:00Z 2017-10-02T01:12:49Z 373cbeecea8286a2b66c97b1b157ec46 583174fbe37d3d5f0d6661be3aad1786 1 Não chegou meu produto Péssimo 2018-08-15T00:00:00Z 2018-08-15T04:10:37Z a2ff510ca4e059c3fefc7a7866571f6f a9953b2f0b1665ac7586cc5a6ac8f58c 4 null null 2017-10-06T00:00:00Z 2017-10-08T22:36:05Z 80c70bc263881ba6525f6cee1d94ac87 ae168dfba236919411fe08f336fefa44 5 null null 2018-03-17T00:00:00Z 2018-04-04T19:41:11Z d21bbc789670eab777d27372ab9094cc 4fc44d78867142c627497b60a7e0228a 5 Ótimo Loja nota 10 2018-07-10T00:00:00Z 2018-07-11T14:10:25Z 7bcb3c758c67f23638262c731493e848 7c9956750739a47dba7a6928ba2f0245 5 null null 2017-09-09T00:00:00Z 2017-10-17T02:25:47Z 0e0190b9db53b689b285d3f3916f8441 79832b7cb59ac6f887088ffd686e1d5e 5 null obrigado pela atençao amim dispensada 2017-12-01T00:00:00Z 2017-12-09T22:58:58Z 66e4430c5bc6b7e3773886bf1c14d912 84cec4f65c7a4f2f54c294a30224a594 5 null null 2017-06-23T00:00:00Z 2017-06-27T00:52:02Z bf566b3910c328733baf7fca7d2be041 a59a15e4b6085c752d338431dc68d464 4 null null 2017-11-01T00:00:00Z 2017-11-01T20:25:30Z fe3db7c069d694bab50cc43463f91608 2ca73e2ff9e3a186ad1e1ffb9b1d9c10 5 null A compra foi realizada


## 2 - Data Cleaning

Aqui nessa table os dados já estão limpos e tratados. Só iremos escrever na camada silver


## Saving data

In [0]:
save_dataframe(df, format_mode="delta", table_name=tb_name, target_location=target_location)

[LOG] Saving olist_silver.order_reviews delta on dbfs:/FileStore/delta/brazilian_ecommerce/olist_order_reviews_dataset/silver... OK!



## create delta table

TODO: implementar UPSERT

o upsert serve para não precisar reescrever todos os dados, mas aproveitar do Delta para fazer um MERGE, caso um registro antigo tenha uma nova versão e INSERT para os dados que são novos

In [0]:
create_table(table_name=tb_name, target_location=target_location)

[LOG] Creating delta table olist_silver.order_reviews on dbfs:/FileStore/delta/brazilian_ecommerce/olist_order_reviews_dataset/silver... OK!


In [0]:
# exit para fechar a execução
dbutils.notebook.exit("OK")

In [0]:
%sql

select * from olist_bronze.order_reviews

review_id order_id review_score review_comment_title review_comment_message review_creation_date review_answer_timestamp 7bc2406110b926393aa56f80a40eba40 73fc7af87114b39712e6da79b0a377eb 4 null null 2018-01-18T00:00:00Z 2018-01-18T21:46:59Z 80e641a11e56f04c1ad469d5645fdfde a548910a1c6147796b98fdf73dbeba33 5 null null 2018-03-10T00:00:00Z 2018-03-11T03:05:13Z 228ce5500dc1d8e020d8d1322874b6f0 f9e4b658b201a9f2ecdecbb34bed034b 5 null null 2018-02-17T00:00:00Z 2018-02-18T14:36:24Z e64fb393e7b32834bb789ff8bb30750e 658677c97b385a9be170737859d3511b 5 null Recebi bem antes do prazo estipulado. 2017-04-21T00:00:00Z 2017-04-21T22:02:06Z f7c4243c7fe1938f181bec41a392bdeb 8e6bfb81e283fa7e4f11123a3fb894f1 5 null Parabéns lojas lannister adorei comprar pela Internet seguro e prático Parabéns a todos feliz Páscoa 2018-03-01T00:00:00Z 2018-03-02T10:26:53Z 15197aa66ff4d0650b5434f1b46cda19 b18dcdf73be66366873cd26c5724d1dc 1 null null 2018-04-13T00:00:00Z 2018-04-16T00:39:37Z 07f9bee5d1b850860defd761afa7ff16 e48aa0d2dcec3a2e87348811bcfdf22b 5 null null 2017-07-16T00:00:00Z 2017-07-18T19:30:34Z 7c6400515c67679fbee952a7525281ef c31a859e34e3adac22f376954e19b39d 5 null null 2018-08-14T00:00:00Z 2018-08-14T21:36:06Z a3f6f7f6f433de0aefbb97da197c554c 9c214ac970e84273583ab523dfafd09b 5 null null 2017-05-17T00:00:00Z 2017-05-18T12:05:37Z 8670d52e15e00043ae7de4c01cc2fe06 b9bf720beb4ab3728760088589c62129 4 recomendo aparelho eficiente. no site a marca do aparelho esta impresso como 3desinfector e ao chegar esta com outro nome...atualizar com a marca correta uma vez que é o mesmo aparelho 2018-05-22T00:00:00Z 2018-05-23T16:45:47Z c9cfd2d5ab5911836ababae136c3a10c cdf9aa68e72324eeb25c7de974696ee2 5 null null 2017-12-23T00:00:00Z 2017-12-26T14:36:03Z 96052551d87e5f62e6c9f6974ec392e9 3d374c9e46530bb5ed4a7648915306a6 5 null null 2017-12-19T00:00:00Z 2017-12-20T10:25:22Z 4b49719c8a200003f700d3d986ea1a19 9d6f15f95d01e79bd1349cc208361f09 4 null Mas um pouco ,travando...pelo valor ta Boa.
 2018-02-16T00:00:00Z 2018-02-20T10:52:22Z 23f75a37effc35d9a915b4e1ad483793 2eaf8e099d871cd5c22b83b5ea8f6e0e 4 null null 2018-03-28T00:00:00Z 2018-03-30T15:10:55Z 9a0abbb668bafb95a6d2b05db43284c4 d7bd0e4afdf94846eb73642b4e3e75c3 3 null null 2017-04-30T00:00:00Z 2017-05-03T00:02:22Z 3948b09f7c818e2d86c9a546758b2335 e51478e7e277a83743b6f9991dbfa3fb 5 Super recomendo Vendedor confiável, produto ok e entrega antes do prazo. 2018-05-23T00:00:00Z 2018-05-24T03:00:01Z 9314d6f9799f5bfba510cc7bcd468c01 0dacf04c5ad59fd5a0cc1faa07c34e39 2 null GOSTARIA DE SABER O QUE HOUVE, SEMPRE RECEBI E ESSA COMPRA AGORA ME DECPCIONOU 2018-01-18T00:00:00Z 2018-01-20T21:25:45Z 8e15a274d95600fa14f8be64e37a0e67 ff1581e08b3011021e7c7de592ddc81e 5 null null 2018-03-24T00:00:00Z 2018-03-26T15:58:32Z fdbdb2629a7cde0f66657acc92084e7f 70a752414a13d09cc1f2b437b914b28e 3 null null 2017-09-29T00:00:00Z 2017-10-02T01:12:49Z 373cbeecea8286a2b66c97b1b157ec46 583174fbe37d3d5f0d6661be3aad1786 1 Não chegou meu produto Péssimo 2018-08-15T00:00:00Z 2018-08-15T04:10:37Z a2ff510ca4e059c3fefc7a7866571f6f a9953b2f0b1665ac7586cc5a6ac8f58c 4 null null 2017-10-06T00:00:00Z 2017-10-08T22:36:05Z 80c70bc263881ba6525f6cee1d94ac87 ae168dfba236919411fe08f336fefa44 5 null null 2018-03-17T00:00:00Z 2018-04-04T19:41:11Z d21bbc789670eab777d27372ab9094cc 4fc44d78867142c627497b60a7e0228a 5 Ótimo Loja nota 10 2018-07-10T00:00:00Z 2018-07-11T14:10:25Z 7bcb3c758c67f23638262c731493e848 7c9956750739a47dba7a6928ba2f0245 5 null null 2017-09-09T00:00:00Z 2017-10-17T02:25:47Z 0e0190b9db53b689b285d3f3916f8441 79832b7cb59ac6f887088ffd686e1d5e 5 null obrigado pela atençao amim dispensada 2017-12-01T00:00:00Z 2017-12-09T22:58:58Z 66e4430c5bc6b7e3773886bf1c14d912 84cec4f65c7a4f2f54c294a30224a594 5 null null 2017-06-23T00:00:00Z 2017-06-27T00:52:02Z bf566b3910c328733baf7fca7d2be041 a59a15e4b6085c752d338431dc68d464 4 null null 2017-11-01T00:00:00Z 2017-11-01T20:25:30Z fe3db7c069d694bab50cc43463f91608 2ca73e2ff9e3a186ad1e1ffb9b1d9c10 5 null A compra foi realizada